In [2]:
import pandas as pd
pd.pandas.set_option('display.max_columns', None)
import numpy as np
import sklearn
from ner import ner
from ner_functions import get_dict_entities_confidence_score
#from ner_functions import ner_organization_entity
from presidio_analyzer import AnalyzerEngine, BatchAnalyzerEngine, RecognizerRegistry


In [3]:
from typing import List
import pprint

from presidio_analyzer import AnalyzerEngine, PatternRecognizer, EntityRecognizer, Pattern, RecognizerResult
from presidio_analyzer.recognizer_registry import RecognizerRegistry
from presidio_analyzer.nlp_engine import NlpEngine, SpacyNlpEngine, NlpArtifacts, NlpEngineProvider
from presidio_analyzer.context_aware_enhancers import LemmaContextAwareEnhancer

In [3]:
import spacy
spacy.load("en_core_web_lg")

## Studying NER

In [3]:
df = pd.read_csv("dataset/table_order.csv")
pd.pandas.set_option('display.max_columns', None)
df

orderNumber productCode  quantityOrdered  priceEach  orderLineNumber  \
0           10100    S18_1749               30     136.00                3   
1           10100    S18_2248               50      55.09                2   
2           10100    S18_4409               22      75.46                4   
3           10100    S24_3969               49      35.29                1   
4           10101    S18_2325               25     108.06                4   
...           ...         ...              ...        ...              ...   
2991        10425    S24_2300               49     127.79                9   
2992        10425    S24_2840               31      31.82                5   
2993        10425    S32_1268               41      83.79               11   
2994        10425    S32_2509               11      50.32                6   
2995        10425    S50_1392               18      94.92                2   

       orderDate requiredDate shippedDate      status                comments  \
0     2003-01-06   2003-01-13  2003-01-10     Shipped                     NaN   
1     2003-01-06   2003-01-13  2003-01-10     Shipped                     NaN   
2     2003-01-06   2003-01-13  2003-01-10     Shipped                     NaN   
3     2003-01-06   2003-01-13  2003-01-10     Shipped                     NaN   
4     2003-01-09   2003-01-18  2003-01-11     Shipped  Check on availability.   
...          ...          ...         ...         ...                     ...   
2991  2005-05-31   2005-06-07         NaN  In Process                     NaN   
2992  2005-05-31   2005-06-07         NaN  In Process                     NaN   
2993  2005-05-31   2005-06-07         NaN  In Process                     NaN   
2994  2005-05-31   2005-06-07         NaN  In Process                     NaN   
2995  2005-05-31   2005-06-07         NaN  In Process                     NaN   

      customerNumber                  customerName contactLastName  \
0                363  Online Diecast Creations Co.           Young   
1                363  Online Diecast Creations Co.           Young   
2                363  Online Diecast Creations Co.           Young   
3                363  Online Diecast Creations Co.           Young   
4                128          Blauer See Auto, Co.          Keitel   
...              ...                           ...             ...   
2991             119             La Rochelle Gifts         Labrune   
2992             119             La Rochelle Gifts         Labrune   
2993             119             La Rochelle Gifts         Labrune   
2994             119             La Rochelle Gifts         Labrune   
2995             119             La Rochelle Gifts         Labrune   

     contactFirstName              phone                  addressLine1  \
0             Dorothy         6035558647      2304 Long Airport Avenue   
1             Dorothy         6035558647      2304 Long Airport Avenue   
2             Dorothy         6035558647      2304 Long Airport Avenue   
3             Dorothy         6035558647      2304 Long Airport Avenue   
4              Roland  +49 69 66 90 2555                 Lyonerstr. 34   
...               ...                ...                           ...   
2991          Janine          40.67.8555  67, rue des Cinquante Otages   
2992          Janine          40.67.8555  67, rue des Cinquante Otages   
2993          Janine          40.67.8555  67, rue des Cinquante Otages   
2994          Janine          40.67.8555  67, rue des Cinquante Otages   
2995          Janine          40.67.8555  67, rue des Cinquante Otages   

     addressLine2       city state postalCode  country  \
0             NaN     Nashua    NH      62005      USA   
1             NaN     Nashua    NH      62005      USA   
2             NaN     Nashua    NH      62005      USA   
3             NaN     Nashua    NH      62005      USA   
4             NaN  Frankfurt   NaN      60528  Germany   
...           ... 

In [23]:
df = df.sample(n=min(1000, df.shape[0])) 


In [24]:
analyzer = AnalyzerEngine(supported_languages=["en", "fr"])
batch_analyzer = BatchAnalyzerEngine(analyzer_engine=analyzer)

In [25]:
analyzer_results = list(batch_analyzer.analyze_dict(df.to_dict(orient="list"), language="en"))

In [26]:
analyzer_results

[DictAnalyzerResult(key='orderNumber', value=[10232, 10312, 10244, 10114, 10127, 10163, 10381, 10109, 10307, 10225, 10206, 10373, 10248, 10149, 10271, 10333, 10306, 10245, 10200, 10179, 10196, 10146, 10339, 10383, 10252, 10388, 10221, 10304, 10358, 10340, 10195, 10348, 10371, 10117, 10179, 10393, 10106, 10412, 10227, 10135, 10197, 10340, 10425, 10248, 10407, 10359, 10223, 10425, 10313, 10223, 10119, 10139, 10107, 10133, 10380, 10380, 10263, 10287, 10143, 10416, 10212, 10393, 10357, 10164, 10332, 10285, 10197, 10122, 10106, 10296, 10217, 10246, 10181, 10358, 10266, 10350, 10104, 10411, 10140, 10263, 10288, 10124, 10403, 10360, 10236, 10165, 10155, 10350, 10197, 10396, 10201, 10135, 10405, 10331, 10319, 10181, 10121, 10204, 10155, 10155, 10331, 10311, 10232, 10182, 10381, 10129, 10259, 10310, 10203, 10235, 10114, 10142, 10296, 10106, 10392, 10140, 10262, 10167, 10342, 10299, 10105, 10200, 10305, 10108, 10379, 10342, 10389, 10103, 10344, 10327, 10276, 10138, 10336, 10313, 10182, 10117, 10

In [44]:
#questo ciclo controlla per ogni colonna, se il suo tipo è object. Se è object, allora aggiunge al dizionario l 
#un'entrata la cui chiave sarà il nome della colonna e il cui valore è la lista delle entity  delle varie liste 
#presenti in recognizer_results solo se queste liste non sono vuote
l = {}
for w, j in zip(df.columns, analyzer_results):
        if df[w].dtype == 'object':
                l[w] = [i[0].entity_type for i in j.recognizer_results if len(i) > 0]

In [45]:
l

{'productCode': ['PERSON',
  'PERSON',
  'PERSON',
  'LOCATION',
  'NRP',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'NRP',
  'PERSON',
  'PERSON',
  'NRP',
  'PHONE_NUMBER',
  'PERSON',
  'PERSON',
  'PHONE_NUMBER',
  'PERSON',
  'PHONE_NUMBER',
  'PERSON',
  'PERSON',
  'NRP',
  'NRP',
  'LOCATION',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PHONE_NUMBER',
  'LOCATION',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PHONE_NUMBER',
  'LOCATION',
  'PERSON',
  'NRP',
  'NRP',
  'PERSON',
  'PERSON',
  'NRP',
  'PERSON',
  'PHONE_NUMBER',
  'PERSON',
  'PERSON',
  'LOCATION',
  'PERSON',
  'PERSON',
  'NRP',
  'NRP',
  'NRP',
  'LOCATION',
  'PERSON',
  'PHONE_NUMBER',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PERSON',
  'PHONE_NUMBER',
  'LOCATION',
  'PHONE_NUMBER',
  'PHONE_NUMBER',
  'PERSON',
  'LOCATION',
  'PERSON',
  'PHO

In [46]:
list_entities = {}
cols = [col for col in df.columns]

In [47]:
cols

['orderNumber',
 'productCode',
 'quantityOrdered',
 'priceEach',
 'orderLineNumber',
 'orderDate',
 'requiredDate',
 'shippedDate',
 'status',
 'comments',
 'customerNumber',
 'customerName',
 'contactLastName',
 'contactFirstName',
 'phone',
 'addressLine1',
 'addressLine2',
 'city',
 'state',
 'postalCode',
 'country',
 'salesRepEmployeeNumber',
 'creditLimit',
 'productName',
 'productLine',
 'productScale',
 'productVendor',
 'productDescription',
 'quantityInStock',
 'buyPrice',
 'MSRP']

In [48]:
for col in cols:
        list_entities[col] = None

In [49]:
#creo lista con solo le chiavi (colonne) la cui lista di valori contiene 
#un numero di elementi maggiore di 0.1 * il numero di rows nel campione
cols = [col for col in l.keys() if len(l[col]) > 0.1 * df.shape[0]]
cols

['orderDate',
 'requiredDate',
 'shippedDate',
 'comments',
 'customerName',
 'contactLastName',
 'contactFirstName',
 'phone',
 'addressLine1',
 'addressLine2',
 'city',
 'state',
 'postalCode',
 'country',
 'productName',
 'productLine',
 'productScale',
 'productVendor',
 'productDescription']

In [50]:
for col in cols:
    lst = [i for i in l[col]]
    if ('LOCATION' in lst) and ('name' not in col.lower()) and (
            len([i for i in l[col] if i == 'LOCATION']) > 0.1 * df.shape[0]):
            #il secondo elemento è una sorta di probabilità/confidenza che quella colonna sia di quel determinato tipo
        list_entities[col] = ['LOCATION', len([i for i in l[col] if i == 'LOCATION'])/df.shape[0]]
    else:
        most_freq = max(set(lst), key=lst.count)
        list_entities[col] = [most_freq, len([i for i in lst if i == most_freq])/df.shape[0]]

In [51]:
loc_cols = [[i, list_entities[i][0]] for i in list_entities.keys() if list_entities[i] is not None]
loc_cols

[['orderDate', 'DATE_TIME'],
 ['requiredDate', 'DATE_TIME'],
 ['shippedDate', 'DATE_TIME'],
 ['comments', 'LOCATION'],
 ['customerName', 'PERSON'],
 ['contactLastName', 'PERSON'],
 ['contactFirstName', 'PERSON'],
 ['phone', 'PHONE_NUMBER'],
 ['addressLine1', 'LOCATION'],
 ['addressLine2', 'LOCATION'],
 ['city', 'LOCATION'],
 ['state', 'LOCATION'],
 ['postalCode', 'DATE_TIME'],
 ['country', 'LOCATION'],
 ['productName', 'LOCATION'],
 ['productLine', 'LOCATION'],
 ['productScale', 'LOCATION'],
 ['productVendor', 'LOCATION'],
 ['productDescription', 'LOCATION']]

In [52]:
loc_cols = [i[0] for i in loc_cols if i[1] == 'LOCATION']
loc_cols

['comments',
 'addressLine1',
 'addressLine2',
 'city',
 'state',
 'country',
 'productName',
 'productLine',
 'productScale',
 'productVendor',
 'productDescription']

In [53]:
addresses = ['street', 'rue', 'via', 'square', 'avenue', 'place', 'strada']
for col in loc_cols:
    list_addresses = [i for i in df[col].fillna('none') if any(ele in i.lower() for ele in addresses)]
    if len(list_addresses) > 0.1 * int(df.shape[0]):
        list_entities[col] = ['ADDRESS', len(list_addresses)/int(df.shape[0])]


In [16]:
list_addresses

[]

In [17]:
list_entities #è un dizionario chiave/colonna: [entity_type, confidence]

{'orderNumber': None,
 'productCode': None,
 'quantityOrdered': None,
 'priceEach': None,
 'orderLineNumber': None,
 'orderDate': ['DATE_TIME', 1.0],
 'requiredDate': ['DATE_TIME', 1.0],
 'shippedDate': ['DATE_TIME', 0.947],
 'status': None,
 'comments': ['LOCATION', 0.745],
 'customerNumber': None,
 'customerName': ['PERSON', 0.076],
 'contactLastName': ['PERSON', 0.505],
 'contactFirstName': ['PERSON', 0.817],
 'phone': ['PHONE_NUMBER', 0.57],
 'addressLine1': ['ADDRESS', 0.24],
 'addressLine2': ['LOCATION', 0.808],
 'city': ['LOCATION', 0.783],
 'state': ['LOCATION', 0.69],
 'postalCode': ['DATE_TIME', 0.057],
 'country': ['LOCATION', 1.0],
 'salesRepEmployeeNumber': None,
 'creditLimit': None,
 'productName': ['LOCATION', 0.101],
 'productLine': ['LOCATION', 0.101],
 'productScale': ['LOCATION', 0.101],
 'productVendor': ['LOCATION', 0.101],
 'productDescription': ['LOCATION', 0.101],
 'quantityInStock': None,
 'buyPrice': None,
 'MSRP': None}

## Trying to improve ner function

In [4]:
df = pd.read_csv("dataset/table_order.csv")


In [5]:
df = df.sample(n=min(1000, df.shape[0]))

In [6]:
df = df.fillna(0)

In [7]:
df

orderNumber productCode  quantityOrdered  priceEach  orderLineNumber  \
561         10163    S18_2949               31     101.31                2   
971         10203    S18_1889               45      73.15                4   
2087        10321    S24_3856               26     137.62               13   
267         10129    S24_3151               41      81.43                4   
2479        10363    S12_3990               34      68.63                5   
...           ...         ...              ...        ...              ...   
2749        10394    S32_2509               36      47.08                3   
556         10162    S18_4409               39      86.51               10   
952         10200   S700_2834               39     115.09                2   
2739        10393    S24_2300               33     112.46                2   
2079        10321    S18_3232               33     164.26               11   

       orderDate requiredDate shippedDate   status  \
561   2003-10-20   2003-10-27  2003-10-24  Shipped   
971   2003-12-02   2003-12-11  2003-12-07  Shipped   
2087  2004-11-04   2004-11-12  2004-11-07  Shipped   
267   2003-06-12   2003-06-18  2003-06-14  Shipped   
2479  2005-01-06   2005-01-12  2005-01-10  Shipped   
...          ...          ...         ...      ...   
2749  2005-03-15   2005-03-25  2005-03-19  Shipped   
556   2003-10-18   2003-10-26  2003-10-19  Shipped   
952   2003-12-01   2003-12-09  2003-12-06  Shipped   
2739  2005-03-11   2005-03-22  2005-03-14  Shipped   
2079  2004-11-04   2004-11-12  2004-11-07  Shipped   

                                               comments  customerNumber  \
561                                                   0             424   
971                                                   0             141   
2087                                                  0             462   
267                                                   0             324   
2479                                                  0             334   
...                                                 ...             ...   
2749                                                  0             141   
556                                                   0             321   
952                                                   0             211   
2739  They want to reevaluate their terms agreement ...             323   
2079                                                  0             462   

                     customerName contactLastName contactFirstName  \
561          Classic Legends Inc.       Hernandez            Maria   
971        Euro+ Shopping Channel          Freyre           Diego    
2087             FunGiftIdeas.com         Benitez          Violeta   
267      Stylish Desk Decors, Co.           Brown             Ann    
2479          Suominen Souveniers        Suominen            Kalle   
...                           ...             ...              ...   
2749       Euro+ Shopping Channel          Freyre           Diego    
556      Corporate Gift Ideas Co.           Brown            Julie   
952   King Kong Collectables, Co.             Gao             Mike   
2739   Down Under Souveniers, Inc          Graham             Mike   
2079             FunGiftIdeas.com         Benitez          Violeta   

                phone                 addressLine1   addressLine2  \
561        2125558493             5905 Pompton St.      Suite 750   
971    (91) 555 94 44           C/ Moralzarzal, 86              0   
2087       5085552555            1785 First Street              0   
267    (171) 555-0297               35 King George              0   
2479  +358 9 8045 555  Software Engineering Center         SEC Oy   
...               ...                          ...            ...   
2749   (91) 555 94 44           C/ Moralzarzal, 86              0   
556        6505551386              7734 Strong St.              0   
952    +852 2251 1555          Bank of China Tower  1 Gar

In [8]:
addresses = ['Street', 'Rue', 'Via', 'Square', 'Avenue', 'Place', 'Strada', 'St', 'Lane', 
    'Road', 'Boulevard', 'Ln', "Rd", "Highway" "Drive", "Av", "Hwy", "Blvd", "Corso", "Piazza", 
    "Calle", "Plaza", "Avenida", "Rambla", "C/"]

In [9]:
addresses_recognizer = PatternRecognizer(supported_entity="ADDRESS", deny_list=addresses)


In [10]:
#using a roberta-based language model to improve performance
'''configuration = {
    "nlp_engine_name": "spacy",
    "models": [{"lang_code": "en", "model_name": "en_core_web_trf"}],
}

# Create NLP engine based on configuration
provider = NlpEngineProvider(nlp_configuration=configuration)
nlp_engine_robertaBased = provider.create_engine()

# Pass the created NLP engine and supported_languages to the AnalyzerEngine
analyzer = AnalyzerEngine(
    nlp_engine = nlp_engine_robertaBased, 
    supported_languages=["en", "fr", "es", "it"]
) '''

'configuration = {\n    "nlp_engine_name": "spacy",\n    "models": [{"lang_code": "en", "model_name": "en_core_web_trf"}],\n}\n\n# Create NLP engine based on configuration\nprovider = NlpEngineProvider(nlp_configuration=configuration)\nnlp_engine_robertaBased = provider.create_engine()\n\n# Pass the created NLP engine and supported_languages to the AnalyzerEngine\nanalyzer = AnalyzerEngine(\n    nlp_engine = nlp_engine_robertaBased, \n    supported_languages=["en", "fr", "es", "it"]\n) '

In [11]:
analyzer = AnalyzerEngine(supported_languages=["en", "fr"])
analyzer.registry.add_recognizer(addresses_recognizer)
batch_analyzer = BatchAnalyzerEngine(analyzer_engine=analyzer)

In [12]:
analyzer_results = list(batch_analyzer.analyze_dict(df.to_dict(orient="list"), language="en"))

In [13]:
analyzer_results

[DictAnalyzerResult(key='orderNumber', value=[10163, 10203, 10321, 10129, 10363, 10168, 10246, 10218, 10187, 10357, 10204, 10215, 10247, 10281, 10252, 10210, 10131, 10184, 10250, 10175, 10222, 10201, 10415, 10273, 10389, 10316, 10352, 10425, 10308, 10347, 10382, 10351, 10159, 10425, 10300, 10220, 10276, 10162, 10304, 10251, 10233, 10162, 10390, 10120, 10251, 10337, 10280, 10227, 10348, 10401, 10368, 10378, 10135, 10181, 10363, 10367, 10412, 10182, 10209, 10301, 10357, 10373, 10265, 10199, 10350, 10224, 10220, 10339, 10232, 10401, 10304, 10273, 10203, 10138, 10390, 10282, 10279, 10270, 10353, 10339, 10326, 10206, 10287, 10356, 10121, 10289, 10425, 10291, 10222, 10296, 10287, 10249, 10131, 10207, 10275, 10316, 10278, 10409, 10241, 10266, 10273, 10120, 10229, 10283, 10280, 10398, 10275, 10379, 10122, 10119, 10314, 10316, 10266, 10197, 10167, 10105, 10343, 10163, 10310, 10159, 10207, 10163, 10107, 10132, 10304, 10339, 10185, 10385, 10240, 10276, 10203, 10301, 10181, 10142, 10401, 10407, 10

In [14]:
df.columns

Index(['orderNumber', 'productCode', 'quantityOrdered', 'priceEach',
       'orderLineNumber', 'orderDate', 'requiredDate', 'shippedDate', 'status',
       'comments', 'customerNumber', 'customerName', 'contactLastName',
       'contactFirstName', 'phone', 'addressLine1', 'addressLine2', 'city',
       'state', 'postalCode', 'country', 'salesRepEmployeeNumber',
       'creditLimit', 'productName', 'productLine', 'productScale',
       'productVendor', 'productDescription', 'quantityInStock', 'buyPrice',
       'MSRP'],
      dtype='object')

In [15]:
list_entities = {}
df_cols = [col for col in df.columns]

In [16]:
for col in df_cols:
    list_entities[col] = None

In [17]:
for col in df_cols:
    #assigning ZIPCODE entity if zipcode in dataset is 'object' type
    if (('postal' in col.lower()) and ('code' in col.lower())) or (('zip' in col.lower()) and (
        'code' in col.lower())) or (('zip' in col.lower())):
        list_entities[col] = ['ZIPCODE', 1.0]
        #assigning CREDIT_CARD_NUMBER entity if credit card number in dataset is 'object' type
    elif (('credit' in col.lower()) or ('card' in col.lower())) and ('number' in col.lower()):
        list_entities[col] = ['CREDIT_CARD_NUMBER', 1.0]

In [18]:
dict_object_entity = {}
for w, j in zip(df.columns, analyzer_results):
    if df[w].dtype == 'object':
        dict_object_entity[w] = [i[0].entity_type for i in j.recognizer_results if len(i) > 0]

In [19]:
cols_object = [col for col in dict_object_entity.keys() if len(dict_object_entity[col]) > 0.1 * df.shape[0]]

In [20]:
cols_object

['orderDate',
 'requiredDate',
 'shippedDate',
 'customerName',
 'contactLastName',
 'contactFirstName',
 'phone',
 'addressLine1',
 'city',
 'state',
 'postalCode',
 'country',
 'productVendor']

In [21]:
for col in cols_object:
    lst = [i for i in dict_object_entity[col]]
    #assigning LOCATION entity
    if ('LOCATION' in lst) and ('name' not in col.lower()) and (
            len([i for i in dict_object_entity[col] if i == 'LOCATION']) > 0.1 * df.shape[0]):
        list_entities[col] = ['LOCATION', len([i for i in dict_object_entity[col] if i == 'LOCATION'])/df.shape[0]]
    #assigning ZIPCODE entity if zipcode in dataset is 'object' type
    elif (('postal' in col.lower()) and ('code' in col.lower())) or (('zip' in col.lower()) and (
            'code' in col.lower())) or (('zip' in col.lower())): 
        list_entities[col] = ['ZIPCODE', 1.0]
    #assigning CREDIT_CARD_NUMBER entity if credit card number in dataset is 'object' type
    elif ((('credit' in col.lower()) or ('card' in col.lower())) and ('number' in col.lower())):
        list_entities[col] = ['CREDIT_CARD_NUMBER', 1.0]
    else:
        most_freq = max(set(lst), key=lst.count)
        list_entities[col] = [most_freq, len([i for i in lst if i == most_freq])/df.shape[0]]

In [22]:
list_entities


{'orderNumber': None,
 'productCode': None,
 'quantityOrdered': None,
 'priceEach': None,
 'orderLineNumber': None,
 'orderDate': ['DATE_TIME', 1.0],
 'requiredDate': ['DATE_TIME', 1.0],
 'shippedDate': ['DATE_TIME', 0.946],
 'status': None,
 'comments': None,
 'customerNumber': None,
 'customerName': ['PERSON', 0.054],
 'contactLastName': ['PERSON', 0.491],
 'contactFirstName': ['PERSON', 0.808],
 'phone': ['PHONE_NUMBER', 0.566],
 'addressLine1': ['ADDRESS', 0.555],
 'addressLine2': None,
 'city': ['LOCATION', 0.78],
 'state': ['LOCATION', 0.134],
 'postalCode': ['ZIPCODE', 1.0],
 'country': ['LOCATION', 1.0],
 'salesRepEmployeeNumber': None,
 'creditLimit': None,
 'productName': None,
 'productLine': None,
 'productScale': None,
 'productVendor': ['PERSON', 0.163],
 'productDescription': None,
 'quantityInStock': None,
 'buyPrice': None,
 'MSRP': None}

## Test ner on other datasets

In [4]:
df_tableOrder = pd.read_csv("dataset/table_order.csv")

In [5]:
df_tableOrder

orderNumber productCode  quantityOrdered  priceEach  orderLineNumber  \
0           10100    S18_1749               30     136.00                3   
1           10100    S18_2248               50      55.09                2   
2           10100    S18_4409               22      75.46                4   
3           10100    S24_3969               49      35.29                1   
4           10101    S18_2325               25     108.06                4   
...           ...         ...              ...        ...              ...   
2991        10425    S24_2300               49     127.79                9   
2992        10425    S24_2840               31      31.82                5   
2993        10425    S32_1268               41      83.79               11   
2994        10425    S32_2509               11      50.32                6   
2995        10425    S50_1392               18      94.92                2   

       orderDate requiredDate shippedDate      status                comments  \
0     2003-01-06   2003-01-13  2003-01-10     Shipped                     NaN   
1     2003-01-06   2003-01-13  2003-01-10     Shipped                     NaN   
2     2003-01-06   2003-01-13  2003-01-10     Shipped                     NaN   
3     2003-01-06   2003-01-13  2003-01-10     Shipped                     NaN   
4     2003-01-09   2003-01-18  2003-01-11     Shipped  Check on availability.   
...          ...          ...         ...         ...                     ...   
2991  2005-05-31   2005-06-07         NaN  In Process                     NaN   
2992  2005-05-31   2005-06-07         NaN  In Process                     NaN   
2993  2005-05-31   2005-06-07         NaN  In Process                     NaN   
2994  2005-05-31   2005-06-07         NaN  In Process                     NaN   
2995  2005-05-31   2005-06-07         NaN  In Process                     NaN   

      customerNumber                  customerName contactLastName  \
0                363  Online Diecast Creations Co.           Young   
1                363  Online Diecast Creations Co.           Young   
2                363  Online Diecast Creations Co.           Young   
3                363  Online Diecast Creations Co.           Young   
4                128          Blauer See Auto, Co.          Keitel   
...              ...                           ...             ...   
2991             119             La Rochelle Gifts         Labrune   
2992             119             La Rochelle Gifts         Labrune   
2993             119             La Rochelle Gifts         Labrune   
2994             119             La Rochelle Gifts         Labrune   
2995             119             La Rochelle Gifts         Labrune   

     contactFirstName              phone                  addressLine1  \
0             Dorothy         6035558647      2304 Long Airport Avenue   
1             Dorothy         6035558647      2304 Long Airport Avenue   
2             Dorothy         6035558647      2304 Long Airport Avenue   
3             Dorothy         6035558647      2304 Long Airport Avenue   
4              Roland  +49 69 66 90 2555                 Lyonerstr. 34   
...               ...                ...                           ...   
2991          Janine          40.67.8555  67, rue des Cinquante Otages   
2992          Janine          40.67.8555  67, rue des Cinquante Otages   
2993          Janine          40.67.8555  67, rue des Cinquante Otages   
2994          Janine          40.67.8555  67, rue des Cinquante Otages   
2995          Janine          40.67.8555  67, rue des Cinquante Otages   

     addressLine2       city state postalCode  country  \
0             NaN     Nashua    NH      62005      USA   
1             NaN     Nashua    NH      62005      USA   
2             NaN     Nashua    NH      62005      USA   
3             NaN     Nashua    NH      62005      USA   
4             NaN  Frankfurt   NaN      60528  Germany   
...           ... 

In [10]:
dict_global_entities = ner_presidio("dataset/table_order.csv")

Starting...


In [12]:
ner_organization_entity("dataset/table_order.csv", dict_global_entities)

{'orderNumber': None,
 'productCode': None,
 'quantityOrdered': None,
 'priceEach': None,
 'orderLineNumber': None,
 'orderDate': ['DATE_TIME', 1.0],
 'requiredDate': ['DATE_TIME', 1.0],
 'shippedDate': ['DATE_TIME', 0.944],
 'status': None,
 'comments': None,
 'customerNumber': None,
 'customerName': ['ORGANIZATION', 0.87],
 'contactLastName': ['PERSON', 0.502],
 'contactFirstName': ['PERSON', 0.84],
 'phone': ['PHONE_NUMBER', 0.576],
 'addressLine1': ['ADDRESS', 0.492],
 'addressLine2': None,
 'city': ['LOCATION', 0.76],
 'state': None,
 'postalCode': ['ZIPCODE', 1.0],
 'country': ['LOCATION', 1.0],
 'salesRepEmployeeNumber': None,
 'creditLimit': None,
 'productName': None,
 'productLine': None,
 'productScale': None,
 'productVendor': ['ORGANIZATION', 0.464],
 'productDescription': None,
 'quantityInStock': None,
 'buyPrice': None,
 'MSRP': None}

#### telco_customer dataset

In [6]:
df_ibm = pd.read_csv("dataset/Telco_customer_churn.csv")


In [7]:
df_ibm

CustomerID  Count        Country       State          City  Zip Code  \
0     3668-QPYBK      1  United States  California   Los Angeles     90003   
1     9237-HQITU      1  United States  California   Los Angeles     90005   
2     9305-CDSKC      1  United States  California   Los Angeles     90006   
3     7892-POOKP      1  United States  California   Los Angeles     90010   
4     0280-XJGEX      1  United States  California   Los Angeles     90015   
...          ...    ...            ...         ...           ...       ...   
7038  2569-WGERO      1  United States  California       Landers     92285   
7039  6840-RESVB      1  United States  California      Adelanto     92301   
7040  2234-XADUH      1  United States  California         Amboy     92304   
7041  4801-JZAZL      1  United States  California  Angelus Oaks     92305   
7042  3186-AJIEK      1  United States  California  Apple Valley     92308   

                    Lat Long   Latitude   Longitude  Gender Senior Citizen  \
0     33.964131, -118.272783  33.964131 -118.272783    Male             No   
1      34.059281, -118.30742  34.059281 -118.307420  Female             No   
2     34.048013, -118.293953  34.048013 -118.293953  Female             No   
3     34.062125, -118.315709  34.062125 -118.315709  Female             No   
4     34.039224, -118.266293  34.039224 -118.266293    Male             No   
...                      ...        ...         ...     ...            ...   
7038  34.341737, -116.539416  34.341737 -116.539416  Female             No   
7039  34.667815, -117.536183  34.667815 -117.536183    Male             No   
7040  34.559882, -115.637164  34.559882 -115.637164  Female             No   
7041     34.1678, -116.86433  34.167800 -116.864330  Female             No   
7042  34.424926, -117.184503  34.424926 -117.184503    Male             No   

     Partner Dependents  Tenure Months Phone Service    Multiple Lines  \
0         No         No              2           Yes                No   
1         No        Yes              2           Yes                No   
2         No        Yes              8           Yes               Yes   
3        Yes        Yes             28           Yes               Yes   
4         No        Yes             49           Yes               Yes   
...      ...        ...            ...           ...               ...   
7038      No         No             72           Yes                No   
7039     Yes        Yes             24           Yes               Yes   
7040     Yes        Yes             72           Yes               Yes   
7041     Yes        Yes             11            No  No phone service   
7042      No         No             66           Yes                No   

     Internet Service      Online Security        Online Backup  \
0                 DSL                  Yes                  Yes   
1         Fiber optic                   No                   No   
2         Fiber optic                   No                   No   
3         Fiber optic                   No                   No   
4         Fiber optic                   No                  Yes   
...               ...                  ...                  ...   
7038               No  No internet service  No internet service   
7039              DSL                  Yes                   No   
7040      Fiber optic                   No                  Yes   
7041              DSL                  Yes                   No   
7042      Fiber optic                  Yes                   No   

        Device Protection         Tech Support         Streaming TV  \
0                      No                   No                   No   
1                      No                   No                   No   
2                     Yes                   No                  Yes   
3                     Yes                  Yes                  Yes   
4                     Yes                   No                  Yes   
...         

In [13]:
dict_gloabl_entities = ner_presidio("dataset/Telco_customer_churn.csv")

Starting...


In [14]:
ner_organization_entity("dataset/Telco_customer_churn.csv", dict_gloabl_entities)

{'CustomerID': ['ORGANIZATION', 0.784],
 'Count': None,
 'Country': ['LOCATION', 1.0],
 'State': ['LOCATION', 1.0],
 'City': ['LOCATION', 0.532],
 'Zip Code': ['ZIPCODE', 1.0],
 'Lat Long': ['US_DRIVER_LICENSE', 0.934],
 'Latitude': None,
 'Longitude': None,
 'Gender': None,
 'Senior Citizen': None,
 'Partner': None,
 'Dependents': None,
 'Tenure Months': None,
 'Phone Service': None,
 'Multiple Lines': None,
 'Internet Service': ['ORGANIZATION', 0.362],
 'Online Security': None,
 'Online Backup': None,
 'Device Protection': None,
 'Tech Support': None,
 'Streaming TV': None,
 'Streaming Movies': None,
 'Contract': ['DATE_TIME', 1.0],
 'Paperless Billing': None,
 'Payment Method': None,
 'Monthly Charges': None,
 'Total Charges': None,
 'Churn Label': None,
 'Churn Value': None,
 'Churn Score': None,
 'CLTV': None,
 'Churn Reason': None}

#### List of real usa addresses

In [18]:
df_USAddresses = pd.read_csv("dataset/list_of_real_usa_addresses.csv")


In [9]:
df_USAddresses[0:50]

address             city state    zip
0             777 Brockton Avenue         Abington    MA   2351
1               30 Memorial Drive             Avon    MA   2322
2             250 Hartford Avenue       Bellingham    MA   2019
3                  700 Oak Street         Brockton    MA   2301
4               66-4 Parkhurst Rd       Chelmsford    MA   1824
5                 591 Memorial Dr         Chicopee    MA   1020
6         55 Brooksby Village Way          Danvers    MA   1923
7               137 Teaticket Hwy    East Falmouth    MA   2536
8        42 Fairhaven Commons Way        Fairhaven    MA   2719
9      374 William S Canning Blvd       Fall River    MA   2721
10               121 Worcester Rd       Framingham    MA   1701
11               677 Timpany Blvd          Gardner    MA   1440
12                 337 Russell St           Hadley    MA   1035
13            295 Plymouth Street          Halifax    MA   2338
14             1775 Washington St          Hanover    MA   2339
15          280 Washington Street           Hudson    MA   1749
16                  20 Soojian Dr        Leicester    MA   1524
17                 11 Jungle Road       Leominster    MA   1453
18          301 Massachusetts Ave        Lunenburg    MA   1462
19                    780 Lynnway             Lynn    MA   1905
20      70 Pleasant Valley Street          Methuen    MA   1844
21        830 Curran Memorial Hwy      North Adams    MA   1247
22           1470 S Washington St  North Attleboro    MA   2760
23                 506 State Road  North Dartmouth    MA   2747
24                742 Main Street     North Oxford    MA   1537
25                     72 Main St    North Reading    MA   1864
26                200 Otis Street     Northborough    MA   1532
27          180 North King Street     Northhampton    MA   1060
28               555 East Main St           Orange    MA   1364
29       555 Hubbard Ave-Suite 12       Pittsfield    MA   1201
30               300 Colony Place         Plymouth    MA   2360
31                 301 Falls Blvd           Quincy    MA   2169
32             36 Paramount Drive          Raynham    MA   2767
33               450 Highland Ave            Salem    MA   1970
34         1180 Fall River Avenue          Seekonk    MA   2771
35               1105 Boston Road      Springfield    MA   1119
36              100 Charlton Road       Sturbridge    MA   1566
37            262 Swansea Mall Dr          Swansea    MA   2777
38                333 Main Street        Tewksbury    MA   1876
39             550 Providence Hwy          Walpole    MA   2081
40                352 Palmer Road             Ware    MA   1082
41     3005 Cranberry Hwy Rt 6 28          Wareham    MA   2538
42                      250 Rt 59          Airmont    NY  10901
43   141 Washington Ave Extension           Albany    NY  12205
44                  13858 Rt 31 W           Albion    NY  14411
45        2055 Niagara Falls Blvd          Amherst    NY  14228
46   101 Sanford Farm Shpg Center        Amsterdam    NY  12010
47               297 Grant Avenue           Auburn    NY  13021
48   4133 Veterans Memorial Drive          Batavia    NY  14020
49  6265 Brockport Spencerport Rd        Brockport    NY  14420

In [10]:
df_USAddresses.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 234 entries, 0 to 233
Data columns (total 4 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   address  234 non-null    object
 1   city     234 non-null    object
 2   state    234 non-null    object
 3   zip      234 non-null    int64 
dtypes: int64(1), object(3)
memory usage: 7.4+ KB


In [2]:
ner_presidio("dataset/list_of_real_usa_addresses.csv")

Starting...


{'address': ['ADDRESS', 0.6153846153846154],
 'city': ['LOCATION', 0.5384615384615384],
 'state': ['LOCATION', 0.6794871794871795],
 'zip': ['ZIPCODE', 1.0]}

#### list of credit number and names

In [5]:
df_creditNumber = pd.read_csv("dataset/1-MB-Test.csv")

In [6]:
df_creditNumber

First and Last Name          SSN   Credit Card Number
0                     NaN          NaN         Visa MC AMEX
1           Robert Aragon  489-36-8350  4929-3813-3266-4295
2           Ashley Borden  514-14-8905  5370-4638-8881-3020
3           Thomas Conley  690-05-5315  4916-4811-5814-8111
4             Susan Davis  421-37-1396  4916-4034-9269-8783
...                   ...          ...                  ...
10551        Albert Iorio  322-84-2303  4916-6734-7572-5037
10552     Charles Jackson  646-44-9083  5218-0144-2703-9288
10553     Teresa Kaminski  465-73-5044  5399-0706-4128-0200
10554            Tim Lowe  044-34-6976  5144-8691-2776-1130
10555     Monte Mceachern  477-36-0304  5527-1247-5046-7802

[10556 rows x 3 columns]

In [7]:
df_creditNumber = df_creditNumber.sample(n=min(1000, df_creditNumber.shape[0]))
df_creditNumber = df_creditNumber.fillna(0)

In [9]:
analyzer = AnalyzerEngine(supported_languages=["en", "fr", "it", "es"])
batch_analyzer = BatchAnalyzerEngine(analyzer_engine=analyzer)

In [11]:
analyzer_results = list(batch_analyzer.analyze_dict(df_creditNumber.to_dict(orient="list"), language="en"))

In [12]:
analyzer_results

[DictAnalyzerResult(key='First and Last Name', value=['Victor\xa0Faulkner', 'Ashley\xa0Borden', 'Lillian\xa0Venson', 'Lynette\xa0Oyola', 'Ashley\xa0Borden', 'Jacki\xa0Russell', 'Christopher\xa0Diaz', 'Monte\xa0Mceachern', 'Charles\xa0Jackson', 'Mireille\xa0Townsend', 'Teresa\xa0Kaminski', 'Robert\xa0Aragon', 'Charles\xa0Jackson', 'Jerome\xa0Munsch', 'Victor\xa0Faulkner', 'Rebecca\xa0Zwick', 'Danny\xa0Reyes', 'Danny\xa0Reyes', 'Rick\xa0Edwards', 'Charles\xa0Jackson', 'Thomas\xa0Santos', 'Adriane\xa0Morrison', 'Lynette\xa0Oyola', 'Gail\xa0Watson', 'Christopher\xa0Diaz', 'Johnson\xa0White', 'Agnes\xa0Nelson', 'Thomas\xa0Conley', 'Adriane\xa0Morrison', 'Ashley\xa0Borden', 'James\xa0Heard', 'Robert\xa0Aragon', 'Agnes\xa0Nelson', 'Mireille\xa0Townsend', 'Stacey\xa0Peacock', 'Victor\xa0Faulkner', 'Lynette\xa0Oyola', 'Monte\xa0Mceachern', 'Jacki\xa0Russell', 'Thomas\xa0Conley', 'Christopher\xa0Diaz', 'Mireille\xa0Townsend', 'Gail\xa0Watson', 'Mark\xa0Hall', 'James\xa0Heard', 'Gail\xa0Watson', 

In [13]:
l = {}
for w, j in zip(df_creditNumber.columns, analyzer_results):
    if df_creditNumber[w].dtype == 'object':
        l[w] = [i[0].entity_type for i in j.recognizer_results if len(i) > 0]

In [15]:
list_entities = {}
cols = [col for col in df_creditNumber.columns]

In [16]:
for col in cols:
    list_entities[col] = None

In [18]:
cols = [col for col in l.keys() if len(l[col]) > 0.1 * df_creditNumber.shape[0]]

In [19]:
cols

['First and Last Name', 'SSN', 'Credit Card Number']

In [32]:
for col in cols:
    lst = [i for i in l[col]]
    #assigning LOCATION entity
    if ('LOCATION' in lst) and ('name' not in col.lower()) and (
            len([i for i in l[col] if i == 'LOCATION']) > 0.1 * df_creditNumber.shape[0]):
        list_entities[col] = ['LOCATION', len([i for i in l[col] if i == 'LOCATION'])/df_creditNumber.shape[0]]
    #assigning ZIPCODE entity if zipcode in dataset is 'object' type
    elif (('postal' in col.lower()) and ('code' in col.lower())) or (('zip' in col.lower()) and (
            'code' in col.lower())) or (('zip' in col.lower())): 
        list_entities[col] = ['ZIPCODE', 1.0]
    elif ((('credit' in col.lower()) or ('card' in col.lower())) and ('number' in col.lower())):
        list_entities[col] = ['CREDIT_CARD_NUMBER', 1.0]
    else:
        most_freq = max(set(lst), key=lst.count)
        list_entities[col] = [most_freq, len([i for i in lst if i == most_freq])/df_creditNumber.shape[0]]

In [33]:
list_entities

{'First and Last Name': ['PERSON', 0.895],
 'SSN': ['US_SSN', 0.938],
 'Credit Card Number': ['CREDIT_CARD_NUMBER', 1.0]}

In [10]:
ner("dataset/1-MB-Test.csv")

Starting...


{'First and Last Name': ['PERSON', 0.905],
 'SSN': ['US_SSN', 0.928],
 'Credit Card Number': ['CREDIT_CARD_NUMBER', 1.0]}

#### Unwanted Calls

In [11]:
ner("dataset/Consumer_Complaints_Data_-_Unwanted_Calls.csv")

Starting...


{'Ticket ID': None,
 'Ticket Created': ['DATE_TIME', 0.951],
 'Date of Issue': ['DATE_TIME', 0.991],
 'Time of Issue': ['DATE_TIME', 0.733],
 'Form': None,
 'Method': None,
 'Issue': None,
 'Caller ID Number': ['PHONE_NUMBER', 0.671],
 'Type of Call or Messge': None,
 'Advertiser Business Number': None,
 'State': ['LOCATION', 0.417],
 'Zip': ['ZIPCODE', 1.0],
 'Location (Center point of the Zip Code)': ['ZIPCODE', 1.0]}

In [12]:
df_unwanted_calls = pd.read_csv('dataset/Consumer_Complaints_Data_-_Unwanted_Calls.csv')

In [13]:
df_unwanted_calls

Ticket ID                Ticket Created Date of Issue Time of Issue  \
0         1000296  05/25/2016 11:15:29 AM +0000    05/01/2016       1:00 pm   
1         1000319  05/25/2016 12:51:35 PM +0000    03/07/2016      12:00 pm   
2         1000322  05/25/2016 12:56:54 PM +0000    05/24/2016       8:08 PM   
3         1000323  05/25/2016 01:00:22 PM +0000    03/07/2016           NaN   
4         1000326  05/25/2016 01:02:31 PM +0000    05/25/2016       7:24 PM   
...           ...                           ...           ...           ...   
426262    1755404  07/05/2017 01:47:49 AM +0000    07/04/2017     9:20 p.m.   
426263    1755411  07/05/2017 02:01:55 AM +0000    07/03/2017      11:00 am   
426264    1755412  07/05/2017 02:02:15 AM +0000    07/03/2017       8:00 am   
426265    1755415  07/05/2017 02:31:26 AM +0000    07/04/2017     5:24 p.m.   
426266    1755429  07/05/2017 03:07:18 AM +0000    07/04/2017     9:59 P.M.   

         Form                                     Method  \
0       Phone                            Internet (VOIP)   
1       Phone                                      Wired   
2       Phone  Wireless (cell phone/other mobile device)   
3       Phone                                      Wired   
4       Phone                            Internet (VOIP)   
...       ...                                        ...   
426262  Phone                                      Wired   
426263  Phone  Wireless (cell phone/other mobile device)   
426264  Phone  Wireless (cell phone/other mobile device)   
426265  Phone  Wireless (cell phone/other mobile device)   
426266  Phone  Wireless (cell phone/other mobile device)   

                                                    Issue Caller ID Number  \
0                                               Robocalls     866-410-0458   
1       Telemarketing (including do not call and spoof...     619-840-7262   
2       Telemarketing (including do not call and spoof...     626-691-9090   
3       Telemarketing (including do not call and spoof...     877-218-8361   
4       Telemarketing (including do not call and spoof...     877-705-6767   
...                                                   ...              ...   
426262                                     Unwanted Calls     812-332-4397   
426263                                     Unwanted Calls     978-248-8466   
426264                                     Unwanted Calls             None   
426265                                     Unwanted Calls             None   
426266                                     Unwanted Calls             None   

            Type of Call or Messge Advertiser Business Number State    Zip  \
0       Autodialed Live Voice Call                        NaN    FL  33324   
1                       Live Voice               619-840-7262    CA  92078   
2                       Live Voice               626-691-9090    NJ  07481   
3                  Abandoned Calls                        NaN    MA  01748   
4                  Abandoned Calls                        NaN    IL  60504   
...                            ...                        ...   ...    ...   
426262             Abandoned Calls                       None    IN  47408   
426263                  Live Voice               978-248-8466    TX  75060   
426264                  Live Voice               855-361-1572    CA  93021   
426265                  Live Voice               904-719-7474    FL  34953   
426266                Text Message               310-388-6768    MD  21209   

       Location (Center point of the Zip Code)  
0              FL 33324\n(26.11294, -80.27429)  
1           CA 92078\n(33.122635, -117.190612)  
2            NJ 07481\n(40.998076, -74.167269)  
3            MA 01748\n(42.224925, -71.537489)  
4       IL 60504-8149\n(41.771365, -88.226673)  
...                                        ...  
426262       IN 47408\n(39.212254, -86.480545)  
426263       TX 75060\n(32.801893, -96.955524)  
426264       CA 93021\n

#### Contact list Austin

In [3]:
df_austin = pd.read_csv("dataset/contact_list_Austin.csv")

In [8]:
df_austin

Department  First Name       Last Name  \
0                                    Department  First Name       Last Name   
1                        Animal Services Office        Joan  Hamilton-Huber   
2                        Austin Code Department      Nathan         Brigmon   
3                        Austin Code Department       Shawn         Lincoln   
4                      Austin Convention Center       Chris       Hernandez   
..                                          ...         ...             ...   
139                    Austin Resource Recovery      Thomas      Montgomery   
140                    Austin Resource Recovery      Thomas      Montgomery   
141  Homeland Security and Emergency Management       Angel          Flores   
142                  Office of the City Auditor       Tyler           Myers   
143            Austin Transportation Department       Diana          Martin   

     Primary Contact                       E-Mail Address  Phone Number  \
0    Primary Contact                       E-Mail Address  Phone Number   
1                NaN  Joan.Hamilton-Huber@austintexas.gov  512-978-0538   
2                NaN       Nathan.Brigmon@austintexas.gov  512-974-6533   
3                NaN        Shawn.Lincoln@austintexas.gov  512-974-9029   
4                NaN      Chris.Hernandez@austintexas.gov  512-404-4031   
..               ...                                  ...           ...   
139               No    Thomas.Montgomery@austintexas.gov  512-974-6022   
140               No    Thomas.Montgomery@austintexas.gov  512-974-6022   
141              Yes         Angel.flores@austintexas.gov  512-974-0477   
142              Yes          Tyler.Myers@austintexas.gov  512-974-2015   
143              Yes         Diana.Martin@austintexas.gov  512-974-4079   

          Role  
0         Role  
1          NaN  
2      Liaison  
3          NaN  
4      Liaison  
..         ...  
139  Publisher  
140  Publisher  
141    Liaison  
142    Liaison  
143    Liaison  

[144 rows x 7 columns]

In [4]:
ner("dataset/contact_list_Austin.csv")

Starting...


{'Department': ['ORGANIZATION', 0.8611111111111112],
 'First Name': ['PERSON', 0.7777777777777778],
 'Last Name': ['PERSON', 0.4027777777777778],
 'Primary Contact': None,
 'E-Mail Address': ['EMAIL_ADDRESS', 0.8888888888888888],
 'Phone Number': ['PHONE_NUMBER', 0.8611111111111112],
 'Role': None}

In [4]:
get_dict_entities_condifence_score("dataset/contact_list_Austin.csv")

Starting...


{'Department': {'entity': 'ORGANIZATION',
  'confidence_score': 0.8611111111111112},
 'First Name': {'entity': 'PERSON', 'confidence_score': 0.7777777777777778},
 'Last Name': {'entity': 'PERSON', 'confidence_score': 0.4027777777777778},
 'Primary Contact': None,
 'E-Mail Address': {'entity': 'EMAIL_ADDRESS',
  'confidence_score': 0.8888888888888888},
 'Phone Number': {'entity': 'PHONE_NUMBER',
  'confidence_score': 0.8611111111111112},
 'Role': None}

In [3]:
dict_global_entities

{'Department': None,
 'First Name': {'entity': 'PERSON', 'confidence_score': 0.7777777777777778},
 'Last Name': {'entity': 'PERSON', 'confidence_score': 0.4027777777777778},
 'Primary Contact': None,
 'E-Mail Address': {'entity': 'EMAIL_ADDRESS',
  'confidence_score': 0.8888888888888888},
 'Phone Number': {'entity': 'PHONE_NUMBER',
  'confidence_score': 0.8611111111111112},
 'Role': None}

#### full-foia-contacts

In [1]:
df_full_noia_contacts = pd.read_csv('dataset/full-noia-contacts.csv')
df_full_noia_contacts

NameError: name 'pd' is not defined

In [16]:
df_full_noia_contacts.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 144 entries, 0 to 143
Data columns (total 7 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Department       144 non-null    object
 1   First Name       132 non-null    object
 2   Last Name        132 non-null    object
 3   Primary Contact  36 non-null     object
 4   E-Mail Address   130 non-null    object
 5   Phone Number     130 non-null    object
 6   Role             86 non-null     object
dtypes: object(7)
memory usage: 8.0+ KB


In [5]:
get_dict_entities_confidence_score("dataset/full-foia-contacts.csv")

Starting...


{'Agency': {'entity': 'ORGANIZATION', 'confidence_score': 0.874},
 'Department': {'entity': 'ORGANIZATION', 'confidence_score': 1.0},
 'Name': {'entity': 'PERSON', 'confidence_score': 0.64},
 'Title': {'entity': 'PERSON', 'confidence_score': 0.35},
 'Room Number': {'entity': 'ORGANIZATION', 'confidence_score': 0.138},
 'Street Address': {'entity': 'ADDRESS', 'confidence_score': 0.28},
 'City': {'entity': 'LOCATION', 'confidence_score': 0.346},
 'State': None,
 'Zip Code': {'entity': 'ZIPCODE', 'confidence_score': 1.0},
 'Telephone': {'entity': 'PHONE_NUMBER', 'confidence_score': 0.898},
 'Fax': {'entity': 'PHONE_NUMBER', 'confidence_score': 0.346},
 'Email Address': {'entity': 'EMAIL_ADDRESS', 'confidence_score': 0.39},
 'Website': {'entity': 'URL', 'confidence_score': 0.34},
 'Online Request Form': None,
 'Notes': {'entity': 'ORGANIZATION', 'confidence_score': 0.142}}

In [18]:
df_full_noia_contacts = df_full_noia_contacts.sample(n=min(500, df_full_noia_contacts.shape[0]))
#df_input = df_input.fillna('/')

In [19]:
for i in df_full_noia_contacts.columns:
    if df_full_noia_contacts[i].dtype == 'object':
        df_full_noia_contacts[i] = df_full_noia_contacts[i].fillna(0)

In [20]:
df_full_noia_contacts

Department First Name Last Name Primary Contact  \
6                    Austin Fire  Christine     Thies             Yes   
74        Austin Code Department     Nathan   Brigmon               0   
9                Mayor & Council          0         0               0   
121     Office of Police Monitor      Farah  Muscadin               0   
132      Public Works Department      Megan      Bell               0   
..                           ...        ...       ...             ...   
5                  Austin Energy      Sarah   Lambert               0   
31    Emergency Medical Services      David  Andersen             Yes   
35                Fleet Services      Tyler    Higdon             Yes   
38   Intergovernmental Relations    Richard    Bailey               0   
14         Austin Public Library      Sarah    Cronin             Yes   

                     E-Mail Address  Phone Number     Role  
6         Christine.Thies@ausps.org  512-974-4119  Liaison  
74   Nathan.Brigmon@austintexas.gov  512-974-6533  Liaison  
9                                 0             0        0  
121  farah.muscadin@austintexas.gov  512-974-9094        0  
132      Megan.Bell@austintexas.gov  512-974-2532        0  
..                              ...           ...      ...  
5    Sarah.Lambert@austinenergy.com  512-505-3535        0  
31         David.Andersen@ausps.org  512-972-7034  Liaison  
35     Tyler.Higdon@austintexas.gov  512-974-1643  Liaison  
38                                0             0        0  
14     Sarah.Cronin@austintexas.gov  512-974-7408  Liaison  

[144 rows x 7 columns]

In [21]:
df_full_noia_contacts.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 144 entries, 6 to 14
Data columns (total 7 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Department       144 non-null    object
 1   First Name       144 non-null    object
 2   Last Name        144 non-null    object
 3   Primary Contact  144 non-null    object
 4   E-Mail Address   144 non-null    object
 5   Phone Number     144 non-null    object
 6   Role             144 non-null    object
dtypes: object(7)
memory usage: 9.0+ KB


In [22]:
addresses = ['Street', 'Rue', 'Via', 'Square', 'Avenue', 'Place', 'Strada', 'St', 'Lane', 
'Road', 'Boulevard', 'Ln', "Rd", "Highway" "Drive", "Av", "Hwy", "Blvd", "Corso", "Piazza", 
"Calle", "Plaza", "Avenida", "Rambla", "C/"]
addresses_recognizer = PatternRecognizer(supported_entity="ADDRESS", deny_list=addresses)


In [23]:
analyzer = AnalyzerEngine(supported_languages=["en", "fr", "it", "es"])

In [24]:
analyzer.registry.add_recognizer(addresses_recognizer)

In [25]:
batch_analyzer = BatchAnalyzerEngine(analyzer_engine=analyzer)

In [26]:
analyzer_results = list(batch_analyzer.analyze_dict(df_full_noia_contacts.to_dict(orient="list"), language="en"))

In [27]:
analyzer_results

[DictAnalyzerResult(key='Department', value=['Austin Fire', 'Austin Code Department', 'Mayor & Council', 'Office of Police Monitor', 'Public Works Department', 'Office of CFO', 'Animal Services Office', 'Corridor Program Implementation Office', 'Equity Office', 'Austin Public Health', 'Downtown Austin Community Court', 'Economic Development', 'Telecom & Regulatory Affairs', 'Austin Public Health', 'Austin Resource Recovery', 'Office of Performance Management', 'Austin Public Library', 'Municipal Court\xa0', 'Aviation Department', 'Public Works Department', 'Intergovernmental Relations', 'Corridor Program Implementation Office', 'Human Resources Department', 'Telecom & Regulatory Affairs', 'Aviation Department', 'Office of the City Auditor', 'Public Works Department', 'Austin Code Department', 'Innovation Office', 'Office of Sustainability', 'Office of Sustainability', "Controller's Office", 'Treasury Office', 'Small & Minority Business Resources', 'Austin Police Department', 'Building 

In [28]:
dict_global_entities = {}
listOf_df_cols = [col for col in df_full_noia_contacts.columns]

for col in listOf_df_cols:
    dict_global_entities[col] = None

In [29]:
dict_global_entities

{'Department': None,
 'First Name': None,
 'Last Name': None,
 'Primary Contact': None,
 'E-Mail Address': None,
 'Phone Number': None,
 'Role': None}

In [30]:
for col in listOf_df_cols:
#assigning ZIPCODE entity
    if (('postal' in col.lower()) and ('code' in col.lower())) or (('zip' in col.lower()) and (
        'code' in col.lower())) or (('zip' in col.lower())):
        dict_global_entities[col] = ['ZIPCODE', 1.0]
#assigning CREDIT_CARD_NUMBER entity
    elif (('credit' in col.lower()) or ('card' in col.lower())) and ('number' in col.lower()):
        dict_global_entities[col] = ['CREDIT_CARD_NUMBER', 1.0]

# the following part creates a python dictionary (keys-> column names, values-> entity type) for columns of type object
dict_typeObject_entities = {}
for w, j in zip(df_full_noia_contacts.columns, analyzer_results):
    if df_full_noia_contacts[w].dtype == 'object':
        dict_typeObject_entities[w] = [i[0].entity_type for i in j.recognizer_results if len(i) > 0]
    
cols = [col for col in dict_typeObject_entities.keys() if len(dict_typeObject_entities[col]) > 0.3 * df_full_noia_contacts.shape[0]]

# this is a very heuristic loop that assigns each object column with an entity

for col in cols:
    lst = [i for i in dict_typeObject_entities[col]]
    #assigning LOCATION entity
    if ('LOCATION' in lst) and ('name' not in col.lower()) and (
            len([i for i in dict_typeObject_entities[col] if i == 'LOCATION']) > 0.1 * df_full_noia_contacts.shape[0]):
        dict_global_entities[col] = ['LOCATION', len([i for i in dict_typeObject_entities[col] 
        if i == 'LOCATION'])/df_full_noia_contacts.shape[0]]
    #assigning ZIPCODE entity if zipcode in dataset is 'object' type
    elif (('postal' in col.lower()) and ('code' in col.lower())) or (('zip' in col.lower()) and (
            'code' in col.lower())) or (('zip' in col.lower())): 
        dict_global_entities[col] = ['ZIPCODE', 1.0]
    #assigning CREDIT_CARD_NUMBER entity if credit card number in dataset is 'object' type
    elif ((('credit' in col.lower()) or ('card' in col.lower())) and ('number' in col.lower())):
        dict_global_entities[col] = ['CREDIT_CARD_NUMBER', 1.0]
    else:
        most_freq = max(set(lst), key=lst.count)
        dict_global_entities[col] = [most_freq, len([i for i in lst if i == most_freq])/df_full_noia_contacts.shape[0]]

In [31]:
dict_global_entities

{'Department': None,
 'First Name': ['PERSON', 0.7777777777777778],
 'Last Name': ['PERSON', 0.4027777777777778],
 'Primary Contact': None,
 'E-Mail Address': ['EMAIL_ADDRESS', 0.8888888888888888],
 'Phone Number': ['PHONE_NUMBER', 0.8611111111111112],
 'Role': None}

In [32]:
for col in dict_global_entities:
    if dict_global_entities[col] is not None:
        dict_global_entities[col] = {'entity': dict_global_entities[col][0],'confidence_score' : dict_global_entities[col][1]}

In [33]:
dict_global_entities

{'Department': None,
 'First Name': {'entity': 'PERSON', 'confidence_score': 0.7777777777777778},
 'Last Name': {'entity': 'PERSON', 'confidence_score': 0.4027777777777778},
 'Primary Contact': None,
 'E-Mail Address': {'entity': 'EMAIL_ADDRESS',
  'confidence_score': 0.8888888888888888},
 'Phone Number': {'entity': 'PHONE_NUMBER',
  'confidence_score': 0.8611111111111112},
 'Role': None}

In [22]:
from transformers import AutoTokenizer, AutoModelForTokenClassification
from transformers import pipeline

tokenizer = AutoTokenizer.from_pretrained("dslim/bert-base-NER")
model = AutoModelForTokenClassification.from_pretrained("dslim/bert-base-NER")

nlp = pipeline("ner", model=model, tokenizer=tokenizer)

In [23]:
for i in df_full_noia_contacts.columns:
    if df_full_noia_contacts[i].dtype == 'object':
        df_full_noia_contacts[i].replace(to_replace = 0, value = '/', inplace =True)

In [24]:
df_full_noia_contacts

Agency  \
20                Foreign Agricultural Service    
280  Centers for Disease Control and Prevention   
309               Headquarters & Privacy Office   
65                            Rural Development   
470        Foreign Claims Settlement Commission   
..                                          ...   
312     U.S. Citizenship & Immigration Services   
475                 Justice Management Division   
642   Office of the Comptroller of the Currency   
713             Office of Resolution Management   
27                    National Appeals Division   

                                  Department                       Name  \
20                 Department of Agriculture            Ellen Dougherty   
280  Department of Health and Human Services           Katherine Norris   
309          Department of Homeland Security  Angela Washington, Acting   
65                 Department of Agriculture               Joseph Shunk   
470                    Department of Justice          Jeremy LaFrancois   
..                                       ...                        ...   
312          Department of Homeland Security             Jill Eggleston   
475                    Department of Justice                          /   
642               Department of the Treasury                Frank Vance   
713           Department of Veterans Affairs                James Horan   
27                 Department of Agriculture          Brenda V. Seegars   

                                      Title              Room Number  \
20                      FOIA Public Liaison  Room 5076-S, Stop 1004    
280                            FOIA Officer        Building 16, D-54   
309                     FOIA Public Liaison                        /   
65                      FOIA Public Liaison                Stop 0706   
470                     FOIA Public Liaison                        /   
..                                      ...                      ...   
312                     FOIA Public Liaison                        /   
475           FOIA Requester Service Center                        /   
642      Freedom of Information Act Officer             Suite 3-E218   
713                     FOIA Public Liaison                        /   
27   FOIA Officer and Legal Affairs Officer                Room 1100   

                   Street Address        City State    Zip Code  \
20                              /           /     /           /   
280       1600 Clifton Road, N.E.     Atlanta    GA       30333   
309                             /           /     /           /   
65   1400 Independence Avenue, SW  Washington    DC  20250-0706   
470                             /           /     /           /   
..                            ...         ...   ...         ...   
312                             /           /     /           /   
475                             /           /     /           /   
642            400 7th Street, SW  Washington    DC       20219   
713                             /           /     /           /   
27         3101 Park Center Drive  Alexandria    VA       22302   

                          Telephone             Fax  \
20                   (202) 720-3448               /   
280                  (770) 488-6399  (404) 235-1852   
309  (202) 343-1743, (866) 431-0486  (202) 343-4011   
65                   (202) 692-0032               /   
470                  (202) 616-6975               /   
..                              ...             ...   
312                  (816) 350-5521               /   
475                  (202) 514-3101               /   
642                  (202) 649-6758               /   
713                  (202) 501-2827               /   
27                   (703) 305-1164  (703) 305-2825   

                          Email Address  \
20                                    /   
280         mailto:FOIARequests@cdc.gov   
309              mailto:foia@hq.dhs.gov   
65                      

In [25]:
dict_of_entities = {}


for i in df_full_noia_contacts.columns:
    if df_full_noia_contacts[i].dtype == 'object' and dict_global_entities[i] == None:
        for j in range (0, df_full_noia_contacts.shape[0]):
            dict_of_entities[i]= [w for w in df_full_noia_contacts[i]]   
                

In [26]:
dict_of_entities

{'Agency': ['Foreign Agricultural Service ',
  'Centers for Disease Control and Prevention',
  'Headquarters & Privacy Office',
  'Rural Development',
  'Foreign Claims Settlement Commission',
  'U.S. Special Operations Command',
  'Region V (Chicago, Columbus, Cleveland, Detroit, Indianapolis, Milwaukee, Minneapolis-St. Paul)',
  'Department of the Air Force',
  'Office of Construction & Facilities Management',
  'United States Marshals Service',
  'Office of Civil Rights',
  'Indian Health Service',
  'Food Safety & Inspection Service',
  'Office of Scientific and Technical Information',
  'Jobs Corps',
  'Office of Community Oriented Policing Services',
  'National Park Service',
  "I don't know which office",
  'Agricultural Marketing Service',
  'Office of Asset Enterprise Management',
  'National Security Division',
  'Department of the Navy',
  'Defense Health Agency',
  'Main Office',
  'Food Safety & Inspection Service',
  'National Appeals Division',
  'Office of the Secretar

In [27]:
for i in dict_of_entities.keys():
    #print(dict_of_entities[i])
    dict_of_entities[i] = nlp(dict_of_entities[i])
    print(i, dict_of_entities[i])

Agency [[{'entity': 'B-ORG', 'score': 0.9989097, 'index': 1, 'word': 'Foreign', 'start': 0, 'end': 7}, {'entity': 'I-ORG', 'score': 0.99831295, 'index': 2, 'word': 'Agricultural', 'start': 8, 'end': 20}, {'entity': 'I-ORG', 'score': 0.99831957, 'index': 3, 'word': 'Service', 'start': 21, 'end': 28}], [{'entity': 'B-ORG', 'score': 0.99890137, 'index': 1, 'word': 'Centers', 'start': 0, 'end': 7}, {'entity': 'I-ORG', 'score': 0.9991509, 'index': 2, 'word': 'for', 'start': 8, 'end': 11}, {'entity': 'I-ORG', 'score': 0.9990734, 'index': 3, 'word': 'Disease', 'start': 12, 'end': 19}, {'entity': 'I-ORG', 'score': 0.99917775, 'index': 4, 'word': 'Control', 'start': 20, 'end': 27}, {'entity': 'I-ORG', 'score': 0.9990388, 'index': 5, 'word': 'and', 'start': 28, 'end': 31}, {'entity': 'I-ORG', 'score': 0.99904674, 'index': 6, 'word': 'Prevention', 'start': 32, 'end': 42}], [{'entity': 'B-ORG', 'score': 0.99656063, 'index': 1, 'word': 'Headquarters', 'start': 0, 'end': 12}, {'entity': 'I-ORG', 'sc

In [27]:
dict_of_entities

{'Agency': [[{'entity': 'B-ORG',
    'score': 0.9913993,
    'index': 1,
    'word': 'Justice',
    'start': 0,
    'end': 7},
   {'entity': 'I-ORG',
    'score': 0.9973035,
    'index': 2,
    'word': 'Management',
    'start': 8,
    'end': 18},
   {'entity': 'I-ORG',
    'score': 0.9926917,
    'index': 3,
    'word': 'Division',
    'start': 19,
    'end': 27}],
  [{'entity': 'B-ORG',
    'score': 0.99931574,
    'index': 1,
    'word': 'National',
    'start': 0,
    'end': 8},
   {'entity': 'I-ORG',
    'score': 0.99934226,
    'index': 2,
    'word': 'Technical',
    'start': 9,
    'end': 18},
   {'entity': 'I-ORG',
    'score': 0.99940133,
    'index': 3,
    'word': 'Information',
    'start': 19,
    'end': 30},
   {'entity': 'I-ORG',
    'score': 0.9993568,
    'index': 4,
    'word': 'Service',
    'start': 31,
    'end': 38}],
  [{'entity': 'B-ORG',
    'score': 0.9975994,
    'index': 1,
    'word': 'O',
    'start': 0,
    'end': 1},
   {'entity': 'I-ORG',
    'score': 

In [ ]:
for col,big_list in keyColumns_valueNone.items():
    flat_entity_list = [entity_dict for sublist in big_list for entity_dict in sublist]
    keyColumns_valueEntities[col] = [entity['entity'] for entity in flat_entity_list]

In [28]:
diz = {}
for i in dict_of_entities.keys():
    #print(i, dict_of_entities[i])
    lst = []
    for j in range(0, len(dict_of_entities[i])):
        if len(dict_of_entities[i][j]) > 0:
            #print(i, dict_of_entities[i][j])
            for w in range(0, len(dict_of_entities[i][j])):
                print(i, dict_of_entities[i][j][w]['entity'])
                lst.append(dict_of_entities[i][j][w]['entity'])
                diz[i] = lst
                

Agency B-ORG
Agency I-ORG
Agency I-ORG
Agency B-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency B-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency B-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency B-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency B-LOC
Agency B-LOC
Agency B-LOC
Agency B-LOC
Agency B-LOC
Agency B-LOC
Agency B-LOC
Agency B-LOC
Agency I-LOC
Agency I-LOC
Agency B-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency B-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency B-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency B-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency B-ORG
Agency I-ORG
Agency I-ORG
Agency B-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency B-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG
Agency I-ORG

In [29]:
diz

{'Agency': ['B-ORG',
  'I-ORG',
  'I-ORG',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'B-LOC',
  'B-LOC',
  'B-LOC',
  'B-LOC',
  'B-LOC',
  'B-LOC',
  'B-LOC',
  'B-LOC',
  'I-LOC',
  'I-LOC',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'B-ORG',


In [36]:
cols = [col for col in diz]

In [37]:
cols

['Agency',
 'Department',
 'Room Number',
 'State',
 'Online Request Form',
 'Notes']

In [39]:
cols = [col for col in diz.keys()]
for col in cols:
    lista = [i for i in diz[col]]
    if (('B-ORG' in lista)) and (
        len([i for i in diz[col] if ((i == 'B-ORG'))]) > 0.1 * df_full_noia_contacts.shape[0]):
        dict_global_entities[col] = ['ORGANIZATION', len([i for i in diz[col] 
                if (i == 'B-ORG')])/df_full_noia_contacts.shape[0]]


In [42]:
lista = diz[col]

In [43]:
lista

['B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG',
 'B-ORG',
 'B-ORG',
 'I-ORG']

In [119]:
dict_global_entities

{'Agency Name': ['ORGANIZATION', 1.0],
 'Address': ['ADDRESS', 0.864406779661017],
 'City': ['LOCATION', 0.711864406779661],
 'State': ['LOCATION', 1.0],
 'Zip Code': ['ZIPCODE', 1.0],
 'Phone Number': ['PHONE_NUMBER', 0.864406779661017],
 'Fax': ['PHONE_NUMBER', 0.7966101694915254],
 'Region Covered': None,
 'Assisted Living Program 1': None,
 'Assisted Living Program 2': None,
 'Assisted Living Program  2E ': None,
 'Assisted Living Program 3': None,
 'Vision Rehabilitation': None,
 'Orientation Mobility ': None,
 'Social Casework Level 1': None,
 'Social Casework Level 2': None,
 'Pre Vocational Young Adults ': None,
 'Diagnostic Vocational Evaluation': None,
 'Academic Instruction': None,
 'Vocational Skills ': None,
 'Work Readiness': None,
 'Work Experience': None,
 'Comprehensive Service Contract': None,
 'Job Placement Service/DVE Contract': None,
 'Location': ['LOCATION', 0.1016949152542373]}

In [7]:
ner('dataset/full-foia-contacts.csv')

Starting...


{'Agency': ['ORGANIZATION', 0.9049531459170014],
 'Department': ['ORGANIZATION', 1.0],
 'Name': ['PERSON', 0.643908969210174],
 'Title': ['PERSON', 0.3386880856760375],
 'Room Number': ['ORGANIZATION', 0.14323962516733602],
 'Street Address': ['ADDRESS', 0.2744310575635877],
 'City': ['LOCATION', 0.3386880856760375],
 'State': ['LOCATION', 0.26238286479250333],
 'Zip Code': ['ZIPCODE', 1.0],
 'Telephone': ['PHONE_NUMBER', 0.891566265060241],
 'Fax': ['PHONE_NUMBER', 0.3493975903614458],
 'Email Address': ['EMAIL_ADDRESS', 0.4029451137884873],
 'Website': ['URL', 0.34002677376171353],
 'Online Request Form': ['URL', 0.09906291834002677],
 'Notes': ['ORGANIZATION', 0.13119143239625167]}

#### Personal Info

In [8]:
ner('dataset/PersonalInfo.csv')

Starting...


{'first_name': ['PERSON', 0.544],
 'last_name': ['PERSON', 0.276],
 'company_name': ['PERSON', 0.314],
 'address': ['ADDRESS', 0.532],
 'city': ['LOCATION', 0.672],
 'county': ['LOCATION', 0.544],
 'state': ['LOCATION', 0.484],
 'zip': ['ZIPCODE', 1.0],
 'phone1': ['PHONE_NUMBER', 0.89],
 'phone2': ['PHONE_NUMBER', 0.918],
 'email': ['EMAIL_ADDRESS', 1.0],
 'web': ['URL', 0.996]}

In [9]:
df_pii = pd.read_csv('dataset/PersonalInfo.csv')

In [10]:
df_pii

first_name  last_name                   company_name  \
0        James       Butt              Benton, John B Jr   
1    Josephine    Darakjy          Chanay, Jeffrey A Esq   
2          Art     Venere            Chemel, James L Cpa   
3        Lenna   Paprocki         Feltz Printing Service   
4      Donette     Foller            Printing Dimensions   
..         ...        ...                            ...   
495    Brittni  Gillaspie                    Inner Label   
496    Raylene      Kampa                     Hermar Inc   
497        Flo   Bookamer   Simonton Howe & Schneider Pc   
498       Jani      Biddy  Warehouse Office & Paper Prod   
499   Chauncey     Motley     Affiliated With Travelodge   

                  address         city      county state    zip        phone1  \
0      6649 N Blue Gum St  New Orleans     Orleans    LA  70116  504-621-8927   
1     4 B Blue Ridge Blvd     Brighton  Livingston    MI  48116  810-292-9388   
2    8 W Cerritos Ave #54   Bridgeport  Gloucester    NJ   8014  856-636-8749   
3             639 Main St    Anchorage   Anchorage    AK  99501  907-385-4412   
4            34 Center St     Hamilton      Butler    OH  45011  513-570-1893   
..                    ...          ...         ...   ...    ...           ...   
495            67 Rv Cent        Boise         Ada    ID  83709  208-709-1235   
496        2 Sw Nyberg Rd      Elkhart     Elkhart    IN  46514  574-499-1454   
497       89992 E 15th St     Alliance   Box Butte    NE  69301  308-726-2182   
498      61556 W 20th Ave      Seattle        King    WA  98104  206-711-6498   
499        63 E Aurora Dr      Orlando      Orange    FL  32804  407-413-4842   

           phone2                          email  \
0    504-845-1427                jbutt@gmail.com   
1    810-374-9840  josephine_darakjy@darakjy.org   
2    856-264-4130                 art@venere.org   
3    907-921-2010          lpaprocki@hotmail.com   
4    513-549-4561         donette.foller@cox.net   
..            ...                            ...   
495  208-206-9848       bgillaspie@gillaspie.com   
496  574-330-1884               rkampa@kampa.org   
497  308-250-6987           flo.bookamer@cox.net   
498  206-395-6284               jbiddy@yahoo.com   
499  407-557-8857        chauncey_motley@aol.com   

                                         web  
0               http://www.bentonjohnbjr.com  
1           http://www.chanayjeffreyaesq.com  
2             http://www.chemeljameslcpa.com  
3        http://www.feltzprintingservice.com  
4          http://www.printingdimensions.com  
..                                       ...  
495                http://www.innerlabel.com  
496                 http://www.hermarinc.com  
497   http://www.simontonhoweschneiderpc.com  
498  http://www.warehouseofficepaperprod.com  
499  http://www.affiliatedwithtravelodge.com  

[500 rows x 12 columns]

### nyscb

In [13]:
ner('dataset/new-york-state-commission-for-the-blind-nyscb-comprehensive-service-contractors-1.csv')

Starting...


{'Agency Name': ['PERSON', 0.13559322033898305],
 'Address': ['ADDRESS', 0.864406779661017],
 'City': ['LOCATION', 0.711864406779661],
 'State': ['LOCATION', 1.0],
 'Zip Code': ['ZIPCODE', 1.0],
 'Phone Number': ['PHONE_NUMBER', 0.864406779661017],
 'Fax': ['PHONE_NUMBER', 0.7966101694915254],
 'Region Covered': None,
 'Assisted Living Program 1': None,
 'Assisted Living Program 2': None,
 'Assisted Living Program  2E ': None,
 'Assisted Living Program 3': None,
 'Vision Rehabilitation': None,
 'Orientation Mobility ': None,
 'Social Casework Level 1': None,
 'Social Casework Level 2': None,
 'Pre Vocational Young Adults ': None,
 'Diagnostic Vocational Evaluation': None,
 'Academic Instruction': None,
 'Vocational Skills ': None,
 'Work Readiness': None,
 'Work Experience': None,
 'Comprehensive Service Contract': None,
 'Job Placement Service/DVE Contract': None,
 'Location': ['LOCATION', 0.1016949152542373]}